<a href="https://colab.research.google.com/github/CUSPADS2022IBX/IBXRidership/blob/main/PLUTO_cleaning.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### PLUTO Cleaning

In [1]:
!pip install wget

  Created wheel for wget: filename=wget-3.2-py3-none-any.whl size=9675 sha256=07b2a3e63526f238acf950da260d86b699d8e639fb3c54324a047669f07543e9
  Stored in directory: /root/.cache/pip/wheels/a1/b6/7c/0e63e34eb06634181c63adacca38b79ff8f35c37e3c13e3c02
Successfully built wget


In [2]:
!pip install pyspark
!pip install pandas fiona shapely pyproj rtree
!pip install geopandas


     |████████████████████████████████| 281.4 MB 22 kB/s 
     |████████████████████████████████| 198 kB 41.4 MB/s 
  Created wheel for pyspark: filename=pyspark-3.2.1-py2.py3-none-any.whl size=281853642 sha256=3d4918f013dc334b25cc9960bda2b6581fd51a9870717f9e799bf7d1e179d622
  Stored in directory: /root/.cache/pip/wheels/9f/f5/07/7cd8017084dce4e93e84e92efd1e1d5334db05f2e83bcef74f
Successfully built pyspark
     |████████████████████████████████| 16.7 MB 5.1 MB/s 
     |████████████████████████████████| 6.3 MB 39.8 MB/s 
     |████████████████████████████████| 1.0 MB 45.8 MB/s 
     |████████████████████████████████| 1.0 MB 5.0 MB/s 


In [3]:
import csv
import json
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import IPython
import wget
%matplotlib inline
IPython.display.set_matplotlib_formats('svg')
pd.plotting.register_matplotlib_converters()
sns.set_style("whitegrid")
import zipfile

import pyspark
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql import types as T
sc = pyspark.SparkContext.getOrCreate()
spark = SparkSession(sc)
spark

#### Reading in PLUTO .csv directly from zip URL

In [4]:
#downloading
!wget 'https://www1.nyc.gov/assets/planning/download/zip/data-maps/open-data/nyc_pluto_21v4_csv.zip'
!unzip 'nyc_pluto_21v4_csv.zip'

--2022-04-16 06:21:47--  https://www1.nyc.gov/assets/planning/download/zip/data-maps/open-data/nyc_pluto_21v4_csv.zip
Resolving www1.nyc.gov (www1.nyc.gov)... 104.127.150.9, 2600:1402:b800:988::1500, 2600:1402:b800:987::1500
Connecting to www1.nyc.gov (www1.nyc.gov)|104.127.150.9|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 93698884 (89M) [application/zip]
Saving to: ‘nyc_pluto_21v4_csv.zip’

nyc_pluto_21v4_csv. 100%[===================>]  89.36M  88.0MB/s    in 1.0s    

2022-04-16 06:21:49 (88.0 MB/s) - ‘nyc_pluto_21v4_csv.zip’ saved [93698884/93698884]

Archive:  nyc_pluto_21v4_csv.zip
  inflating: PLUTODD21v4.pdf         
  inflating: PlutoReadme21v4.pdf     
  inflating: pluto_21v4.csv          


In [5]:
#reading as spark dataframe 
pluto = spark.read.csv('/content/pluto_21v4.csv',header=True)\
.select('BCT2020','lotarea', 'bldgarea', 'comarea', 'resarea',
       'officearea', 'retailarea', 'garagearea', 'strgearea', 'factryarea',
       'otherarea','numbldgs','numfloors','unitsres','unitstotal','assesstot')


In [6]:
#list of column names for iterating 
cols = pluto.columns[1:]

#iterating through spark DF columns to cast to float 
for col_name in cols:
    pluto = pluto.withColumn(col_name, F.col(col_name).cast('float'))

#sums of counts as groupby
pluto_tract = pluto.groupBy('BCT2020').sum()

#list of column names for iterating
cols1 = pluto_tract.columns[1:]

for i in range(len(cols1)):
    pluto_tract = pluto_tract.withColumnRenamed(cols1[i],cols[i])

In [ ]:
pluto_tract.show(5)


#aggregated by station 

+-------+---------+---------+--------+---------+----------+----------+----------+---------+----------+---------+--------+------------------+--------+----------+------------+
|BCT2020|  lotarea| bldgarea| comarea|  resarea|officearea|retailarea|garagearea|strgearea|factryarea|otherarea|numbldgs|         numfloors|unitsres|unitstotal|   assesstot|
+-------+---------+---------+--------+---------+----------+----------+----------+---------+----------+---------+--------+------------------+--------+----------+------------+
|3056600|1258182.0|1254905.0|196353.0| 978845.0|   82590.0|   69635.0|    5550.0|      0.0|       0.0|  38578.0|   575.0|             762.0|   988.0|    1032.0| 5.2304088E7|
|4072300|3602899.0|1899353.0|125662.0|1756701.0|    6791.0|    8100.0|       0.0|      0.0|       0.0| 110771.0|  1045.0|1574.5899999141693|   913.0|     934.0|  9.459345E7|
|4027200|1194838.0| 644470.0| 99013.0| 538597.0|    8594.0|   49467.0|       0.0|   2550.0|       0.0|  36853.0|   617.0| 954.6699

In [ ]:
#could group by census block (~350,169) different groups 
#could aggregate by census tract (~5,000)
#could aggregate by zip (~1700)
#could aggregate by tax lots or tax blocks 

2323

In [7]:
pluto_df = pluto_tract.toPandas()
pluto_df.head()

BCT2020    lotarea   bldgarea   comarea    resarea  officearea  retailarea  \
0  3056600  1258182.0  1254905.0  196353.0   978845.0     82590.0     69635.0   
1  4072300  3602899.0  1899353.0  125662.0  1756701.0      6791.0      8100.0   
2  4027200  1194838.0   644470.0   99013.0   538597.0      8594.0     49467.0   
3  3080200  1428334.0  2334285.0  300431.0  1947838.0     13892.0     93475.0   
4  2033700  2948047.0  1887595.0  370078.0  1400446.0    128057.0     66977.0   

   garagearea  strgearea  factryarea  otherarea  numbldgs  numfloors  \
0      5550.0        0.0         0.0    38578.0     575.0     762.00   
1         0.0        0.0         0.0   110771.0    1045.0    1574.59   
2         0.0     2550.0         0.0    36853.0     617.0     954.67   
3      1215.0        0.0         0.0   191849.0     464.0    1096.43   
4     36040.0     1041.0         0.0   136467.0     663.0    1254.76   

   unitsres  unitstotal    assesstot  
0     988.0      1032.0   52304088.0  
1     913.0       934.0   94593450.0  
2     550.0       595.0   21781104.0  
3    1924.0      2041.0  103270263.0  
4    1256.0      1352.0   66661442.0

In [8]:
import geopandas as gpd

In [9]:
#getting census data 
!wget 'https://www1.nyc.gov/assets/planning/download/zip/data-maps/open-data/nyct2020_22a.zip'
!unzip 'nyct2020_22a.zip'



--2022-04-16 06:22:46--  https://www1.nyc.gov/assets/planning/download/zip/data-maps/open-data/nyct2020_22a.zip
Resolving www1.nyc.gov (www1.nyc.gov)... 104.127.150.9, 2600:1402:b800:988::1500, 2600:1402:b800:987::1500
Connecting to www1.nyc.gov (www1.nyc.gov)|104.127.150.9|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1472942 (1.4M) [application/zip]
Saving to: ‘nyct2020_22a.zip’

nyct2020_22a.zip    100%[===================>]   1.40M  --.-KB/s    in 0.07s   

2022-04-16 06:22:46 (20.2 MB/s) - ‘nyct2020_22a.zip’ saved [1472942/1472942]

Archive:  nyct2020_22a.zip
  inflating: nyct2020_22a/nyct2020.shp  
  inflating: nyct2020_22a/nyct2020.dbf  
  inflating: nyct2020_22a/nyct2020.shx  
  inflating: nyct2020_22a/nyct2020.prj  
  inflating: nyct2020_22a/nyct2020.shp.xml  


In [10]:
#read in shapefile for later merge 
census_geo = gpd.read_file('/content/nyct2020_22a/nyct2020.dbf')

census_geo.shape


(2325, 14)

In [11]:
#read in ACS census data from git 
census_data = pd.read_csv('https://raw.githubusercontent.com/CUSPADS2022IBX/IBXRidership/main/PLUTO%20Data%20Processing/census_tract_data_nyc.csv')

In [12]:
#merge pluto with census data 
pluto_census = pluto_df.merge(census_data.drop_duplicates('BCT2020'),left_on='BCT2020',right_on='BCT2020', how = 'left')
pluto_census.shape

(2323, 51)

In [13]:
#merge with census geometry
pluto_geo = pluto_census.merge(census_geo,left_on='BCT2020',right_on='BoroCT2020',how='left')
pluto_geo.shape

(2323, 65)

In [14]:
#creating geodf 
pluto_gdf = gpd.GeoDataFrame(
    pluto_geo, geometry=pluto_geo['geometry'],crs=census_geo.crs)

In [15]:
#create voronoi polyongs from station points 
stations = pd.read_csv('https://raw.githubusercontent.com/CUSP2021ADS/Data/main/NYCSubwayNodes.csv'); stations

name   id boro        lat       long    lines
0       Greenpoint Av  G26   Bk  40.731352 -73.954449        G
1               21 St  G24    Q  40.744065 -73.949724        G
2            Court Sq  G22    Q  40.746554 -73.943832        G
3               36 St  G20    Q  40.752039 -73.928781      M R
4        Queens Plaza  G21    Q  40.748973 -73.937243    E M R
..                ...  ...  ...        ...        ...      ...
493         City Hall  R24    M  40.713282 -74.006978      R W
494          Canal St  R23    M  40.719527 -74.001775      R W
495         Prince St  R22    M  40.724329 -73.997702      R W
496        8 St - NYU  R21    M  40.730328 -73.992629      R W
497  14 St - Union Sq  R20    M  40.735736 -73.990568  N Q R W

[498 rows x 6 columns]

In [ ]:
#download borough boundary from:
#https://data.cityofnewyork.us/City-Government/Borough-Boundaries/tqmj-j8zm
#OR https://github.com/CUSPADS2022IBX/IBXRidership/tree/main/PLUTO%20Data%20Processing/Borough%20Boundaries


In [16]:
#getting shapefiles from link directly 
!wget 'https://data.cityofnewyork.us/api/geospatial/tqmj-j8zm?method=export&format=Shapefile'
!unzip 'tqmj-j8zm?method=export&format=Shapefile'


--2022-04-16 06:23:33--  https://data.cityofnewyork.us/api/geospatial/tqmj-j8zm?method=export&format=Shapefile
Resolving data.cityofnewyork.us (data.cityofnewyork.us)... 52.206.140.199, 52.206.140.205, 52.206.68.26
Connecting to data.cityofnewyork.us (data.cityofnewyork.us)|52.206.140.199|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [application/zip]
Saving to: ‘tqmj-j8zm?method=export&format=Shapefile’

tqmj-j8zm?method=ex     [ <=>                ] 908.98K  --.-KB/s    in 0.1s    

2022-04-16 06:23:34 (9.10 MB/s) - ‘tqmj-j8zm?method=export&format=Shapefile’ saved [930791]

Archive:  tqmj-j8zm?method=export&format=Shapefile
  inflating: geo_export_3e2b685b-7bac-4f90-835b-89976a979954.dbf  
  inflating: geo_export_3e2b685b-7bac-4f90-835b-89976a979954.shp  
  inflating: geo_export_3e2b685b-7bac-4f90-835b-89976a979954.shx  
  inflating: geo_export_3e2b685b-7bac-4f90-835b-89976a979954.prj  


In [18]:
#convert to gpd, correct crs
#need to copy file path from content directory
boros = gpd.read_file('/content/geo_export_3e2b685b-7bac-4f90-835b-89976a979954.dbf')


boros


boro_code      boro_name    shape_area     shape_leng  \
0        4.0         Queens  3.040206e+09  900269.280485   
1        3.0       Brooklyn  1.934167e+09  728477.954082   
2        5.0  Staten Island  1.623631e+09  325924.002076   
3        1.0      Manhattan  6.366208e+08  359993.126318   
4        2.0          Bronx  1.187194e+09  463868.599917   

                                            geometry  
0  MULTIPOLYGON (((-73.82645 40.59053, -73.82642 ...  
1  MULTIPOLYGON (((-73.86327 40.58388, -73.86381 ...  
2  MULTIPOLYGON (((-74.05051 40.56642, -74.05047 ...  
3  MULTIPOLYGON (((-74.01093 40.68449, -74.01193 ...  
4  MULTIPOLYGON (((-73.89681 40.79581, -73.89694 ...

In [23]:
!pip install contextily
!pip install geovoronoi
!pip install shapely

     |████████████████████████████████| 19.3 MB 62.9 MB/s 
     |████████████████████████████████| 38.1 MB 1.3 MB/s 
  Attempting uninstall: scipy
    Found existing installation: scipy 1.4.1
    Uninstalling scipy-1.4.1:
      Successfully uninstalled scipy-1.4.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
albumentations 0.1.12 requires imgaug<0.2.7,>=0.2.5, but you have imgaug 0.2.9 which is incompatible.


In [24]:
#imports and install for voronoi
import numpy as np
import geopandas as gpd
import contextily as ctx
import matplotlib.pyplot as plt
from shapely.ops import cascaded_union
from geovoronoi.plotting import subplot_for_map, plot_voronoi_polys_with_points_in_area
from geovoronoi import voronoi_regions_from_coords, points_to_coords

In [20]:
#convert stations to geopandas, matching crs 
stations_geo = gpd.GeoDataFrame(stations, geometry=gpd.points_from_xy(stations.long, stations.lat),crs=boros.crs)

In [25]:
fig, ax = plt.subplots(figsize=(12, 10))
boros.plot(ax=ax)
stations_geo.plot(ax=ax, markersize=3.5, color = 'black')
plt.show()

In [26]:
#keep doing voronoi
boros_shape = cascaded_union(boros.geometry)
coords = points_to_coords(stations_geo.geometry)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: ShapelyDeprecationWarning: The 'cascaded_union()' function is deprecated. Use 'unary_union()' instead.
  


In [27]:
#get voronois
poly_shapes, pts = voronoi_regions_from_coords(coords, boros_shape)

In [29]:
#voronoi plot 
fig, ax = subplot_for_map(figsize=(12, 10))


plot_voronoi_polys_with_points_in_area(ax, boros_shape, poly_shapes, coords, pts)
plt.show()

/usr/local/lib/python3.7/dist-packages/descartes/patch.py:65: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  for t in polygon])
/usr/local/lib/python3.7/dist-packages/descartes/patch.py:65: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  for t in polygon])


In [28]:
#some multipolygons turning into polygon lists
voronoi_regions=pd.DataFrame.from_dict(poly_shapes,orient='index')
voronoi_regions

#convert to geopandas
voronoi_gpd = gpd.GeoDataFrame(voronoi_regions, geometry=voronoi_regions[0],crs=boros.crs)

/usr/local/lib/python3.7/dist-packages/pandas/core/dtypes/cast.py:1990: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  result[:] = values


In [29]:
#convert voronoi to new york projection, same as pluto_gdf
voronoi_gpd = voronoi_gpd.to_crs(crs=pluto_gdf.crs)

In [31]:
#!pip install rtree
#!pip install pygeos
import rtree
#import pygeos

In [84]:
voronoi_census = gpd.overlay(voronoi_gpd,pluto_gdf, how='intersection')
#voronoi_census = gpd.sjoin(voronoi_gpd,pluto_gdf, how='right')

#maybe - voronoi_census.area from this - and divide by matching census id 
#voronoi_census.plot(alpha=0.5, edgecolor='k', cmap='tab10');

In [91]:
#getting proportion of area of each intersection between vornoy and census tracts 
voronoi_census['area'] = voronoi_census.area/voronoi_census['Shape_Area']

In [92]:
voronoi_census

/usr/local/lib/python3.7/dist-packages/pandas/core/dtypes/inference.py:383: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  iter(obj)  # Can iterate over it.
/usr/local/lib/python3.7/dist-packages/pandas/core/dtypes/inference.py:384: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  len(obj)  # Has a length associated with it.
/usr/local/lib/python3.7/dist-packages/pandas/io/formats/printing.py:118: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  s = iter(seq)
/usr/local/lib/python3.7/dist-packages/pandas/io/formats/printing.p

0  BCT2020     lotarea  \
0     POLYGON ((-74.19585750848185 40.6231536160957,...  5029102  84052392.0   
1     POLYGON ((-74.10054804434564 40.55855711784107...  5029102  84052392.0   
2     (POLYGON ((-74.19585750848185 40.6231536160957...  5029102  84052392.0   
3     POLYGON ((-74.19585750848185 40.6231536160957,...  5029102  84052392.0   
4     POLYGON ((-74.15811983415615 40.59297343395072...  5029102  84052392.0   
...                                                 ...      ...         ...   
5393  POLYGON ((-73.83090077277144 40.57849590721296...  4092200   6582094.0   
5394  POLYGON ((-73.83090077277144 40.57849590721296...  4092800   8892506.0   
5395  POLYGON ((-73.83090077277144 40.57849590721296...  4093401   9876826.0   
5396  POLYGON ((-73.83090077277144 40.57849590721296...  4093402   5853404.0   
5397  POLYGON ((-73.83090077277144 40.57849590721296...  4091800  12090382.0   

       bldgarea    comarea    resarea  officearea  retailarea  garagearea  \
0     7374546.0  4688905.0  1362738.0    685187.0    509312.0    182613.0   
1     7374546.0  4688905.0  1362738.0    685187.0    509312.0    182613.0   
2     7374546.0  4688905.0  1362738.0    685187.0    509312.0    182613.0   
3     7374546.0  4688905.0  1362738.0    685187.0    509312.0    182613.0   
4     7374546.0  4688905.0  1362738.0    685187.0    509312.0    182613.0   
...         ...        ...        ...         ...         ...         ...   
5393  1787562.0    12000.0  1684036.0         0.0         0.0         0.0   
5394  2436564.0   172003.0  2107145.0     72715.0         0.0         0.0   
5395  2201078.0   203392.0  1822479.0     15104.0     42117.0      8996.0   
5396  2126856.0   225711.0  1815424.0     34255.0     89311.0     36690.0   
5397   176621.0   152490.0    22154.0         0.0         0.0         0.0   

      strgearea  ...  CDEligibil  \
0      250911.0  ...        None   
1      250911.0  ...        None   
2      250911.0  ...        None   
3      250911.0  ...        None   
4      250911.0  ...        None   
...         ...  ...         ...   
5393        0.0  ...        None   
5394        0.0  ...        None   
5395        0.0  ...        None   
5396     2407.0  ...        None   
5397        0.0  ...        None   

                                                NTAName  NTA2020  CDTA2020  \
0         New Springville-Willowbrook-Bulls Head-Travis   SI0204      SI02   
1         New Springville-Willowbrook-Bulls Head-Travis   SI0204      SI02   
2         New Springville-Willowbrook-Bulls Head-Travis   SI0204      SI02   
3         New Springville-Willowbrook-Bulls Head-Travis   SI0204      SI02   
4         New Springville-Willowbrook-Bulls Head-Travis   SI0204      SI02   
...                                                 ...      ...       ...   
5393  Breezy Point-Belle Harbor-Rockaway Park-Broad ...   QN1403      QN14   
5394  Breezy Point-Belle Harbor-Rockaway Park-Broad ...   QN1403      QN14   
5395  Breezy Point-Belle Harbor-Rockaway Park-Broad ...   QN1403      QN14   
5396  Breezy Point-Belle Harbor-Rockaway Park-Broad ...   QN1403      QN14   
5397       Jacob Riis Park-Fort Tilden-Breezy Point Tip   QN8492      QN84   

                                            CDTANAME        GEOID  \
0               SI02 Mid-Island (CD 2 Approximation)  36085029102   
1               SI02 Mid-Island (CD 2 Approximation)  36085029102   
2               SI02 Mid-Island (CD 2 Approximation)  36085029102   
3               SI02 Mid-Island (CD 2 Approximation)  36085029102   
4               SI02 Mid-Island (CD 2 Approximation)  36085029102   
...                                              ...          ...   
5393        QN14 The Rockaways (CD 14 Approximation)  36081092200   
5394        QN14 The Rockaways (CD 14 Approximation)  36081092800   
5395        QN14 The Rockaways (CD 14 Approximation)  36081093401   
5396        QN14 The Rockaways (CD 14 Approximation)  36081093402   
5397  QN84 Jamaica Bay (East) (JIA 84 A

In [92]:
#multiply the calculated proportion to all census data for each row

In [45]:
#groupby voronoi IDs and aggregate/add up all census data 

/usr/local/lib/python3.7/dist-packages/geopandas/base.py:31: UserWarning: The indices of the two GeoSeries are different.
  warn("The indices of the two GeoSeries are different.")


In [ ]:
#match voronoi to each station ID --> re map 

In [38]:
pluto_gdf.shape

(2323, 65)

In [ ]:
#need to convert census tracts to same crs!!

